In [ ]:
#Maps the NIC LEI population to GLEIF
#Exploration of matching methods for institutions that have only name and address in NIC but may have an LEI


In [14]:
import pandas as pd
from fuzzywuzzy import fuzz
from fuzzywuzzy import process

#set display options for pandas dataframes
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)

In [15]:
#get lei map to panel from
#load NIC ID walk
nic_ids = pd.read_csv("/Users/roellk/Desktop/HMDA/hmda-panel/2017/output/panel_lei_map.txt", sep="|", dtype="object")
nic_ids.fillna("-1", inplace=True)
print(len(nic_ids))
#nic_ids

5852


In [18]:
#load GLEIF LEI list
gleif_df = pd.read_csv("../output/lei_info.txt", sep="|", dtype="object")
fill_cols = ["legal_city", "legal_name", "hq_city", "hq_country"]
gleif_df.fillna("-1", inplace=True)
gleif_df = gleif_df[gleif_df.legal_country=="US"]
print(len(gleif_df))
gleif_df.head()

160557


hq_city hq_country             hq_street1 hq_street2  \
2253      -1         US  108, WEST 13TH STREET         -1   
3030      -1         GB  20 ST. DUNSTAN'S HILL         -1   
3141      -1         GB        8 CANADA SQUARE         -1   
3142      -1         GB        8 CANADA SQUARE         -1   
3143      -1         GB        8 CANADA SQUARE         -1   

                    id_lei  legal_city legal_country  \
2253  21380087BAB79DFYRR32  WILMINGTON            US   
3030  2138008LTICA91ZQKQ29  NEW JERSEY            US   
3141  213800H6B1VQJ2WGUW78  WILMINGTON            US   
3142  213800694GO11UR95731  WILMINGTON            US   
3143  213800NAN42LNYBD1Z52  WILMINGTON            US   

                             legal_name legal_post legal_region  \
2253                LION COMMERCIAL LLC      19801           -1   
3030    GROSVENOR BROKERS (AMERICA) LLC      07701           -1   
3141  BENEFICIAL COMMERCIAL CORPORATION      19801           -1   
3142        BENEFICIAL CONNECTICUT INC.      19801           -1   
3143    BENEFICIAL CREDIT SERVICES INC.      19801           -1   

                          legal_street1  \
2253              108, WEST 13TH STREET   
3030                  5 NORTHOVER PLACE   
3141  C/O THE CORPORATION TRUST COMPANY   
3142  C/O THE CORPORATION TRUST COMPANY   
3143  C/O THE CORPORATION TRUST COMPANY   

                                     legal_street2  
2253                                            -1  
3030                                      RED BANK  
3141                            1209 ORANGE STREET  
3142  CORPORATION TRUST CENTER, 1209 ORANGE STREET  
3143  CORPORATION TRUST CENTER, 1209 ORANGE STREET

In [8]:
gleif_df.legal_country.unique()

array(['US'], dtype=object)

In [9]:
#merge panel and gleif data to check on address and name matching
check_df = pd.merge(left=nic_ids, right=gleif_df, on="id_lei", how="left")
display_cols = ["institution_id",
                "id_lei",
                "nm_lgl",
                "legal_name",
                "respondent_city",
                "city",
                "legal_city",
                "hq_city",
                "respondent_state_fips_number",
                "respondent_state_code",  
                "state_cd",
                "street_line1",
                "street_line2",
                "legal_street1",
                "legal_street2",
                "hq_street1",
                "hq_street2",
                "zip_cd",
                "legal_post",
                "legal_region",
                "hq_country",
                "agency_code"]

for col in display_cols:
    if col != "id_lei":
        check_df[col] = check_df[col].apply(lambda x: str(x).lower())

check_df[display_cols]

institution_id                id_lei  \
0            546991                    -1   
1            858528                    -1   
2           3603765  549300XVXVMZ9CDXV530   
3            213538                    -1   
4            724490                    -1   
5           2871099  549300LTKCJV903ZQR25   
6            978239                    -1   
7           3875151                    -1   
8           3872039                    -1   
9            835444                    -1   
10           343396                    -1   
11           296670                    -1   
12            28406  FJMKG323P0YU76XURH25   
13           772008                    -1   
14          3882412                    -1   
15           215710                    -1   
16           368522                    -1   
17          3868881                    -1   
18           580155                    -1   
19           173557                    -1   
20           984258                    -1   
21            14070                    -1   
22           896191                    -1   
23           203986                    -1   
24           968249                    -1   
25           576653                    -1   
26           550635  549300NN5CG5Q640OV05   
27           206174                    -1   
28          4186658                    -1   
29           265087                    -1   
30          3878620                    -1   
31           474919  DZC62HF6UIZYJ08V1J90   
32           920854  54930002ZF7XTZGVKY26   
33            73796                    -1   
34           558574                    -1   
35          4437510                    -1   
36           257756                    -1   
37           670775                    -1   
38          2891622                    -1   
39           215662                    -1   
40           752381                    -1   
41          2512347                    -1   
42           302656  549300WYC8C6REMY4E38   
43           100683                    -1   
44            40798                    -1   
45          3138146  SI7YQSVPFZBSQ878IC17   
46           822387                    -1   
47            23184                    -1   
48           535034                    -1   
49          1972298                    -1   
50           613400  549300IYKILIU506KA05   
51           951698                    -1   
52           646958                    -1   
53          3878460                    -1   
54           194981                    -1   
55          2736291                    -1   
56           281498                    -1   
57           524579                    -1   
58            22794                    -1   
59           649874                    -1   
60           987053  549300SCFU7K14E0J331   
61           877079                    -1   
62           982188                    -1   
63            39756                    -1   
64           945053                    -1   
65          2787770  549300XV8D5BHDJZY155   
66            26998                    -1   
67           219044                    -1   
68            18890                    -1   
69          1001648  549300CP7747DCRW6U68   
70          3958205                    -1   
71           646042                    -1   
72           744984                    -1   
73           866055                    -1   
74            92685                    -1   
75           320052                    -1   
76          3890097                    -1   
77          3806481                    -1   
78          1407932  8VPESZVIXN83ENVWIB56   
79           701950                    -1   
80          3101065  549300WJMSK78N2L9U23   
81            37994                    -1   
82           235594                    -1   
83           653349                    -1   
84          2797359                    -1   
85          3384318  549300LS4IRCYZSRMH20   
86           714389                    -1   
87       72-1591908                    -1   


In [10]:
print(len(check_df[display_cols][(check_df.nm_lgl==check_df.legal_name)&(~check_df.nm_lgl.isin(["nan", "-1"]))]), "rows matched on name")
check_df[display_cols][(check_df.nm_lgl==check_df.legal_name)&(~check_df.nm_lgl.isin(["nan", "-1"]))]

465 rows matched on name


institution_id                id_lei  \
2           3603765  549300XVXVMZ9CDXV530   
5           2871099  549300LTKCJV903ZQR25   
12            28406  FJMKG323P0YU76XURH25   
26           550635  549300NN5CG5Q640OV05   
31           474919  DZC62HF6UIZYJ08V1J90   
32           920854  54930002ZF7XTZGVKY26   
42           302656  549300WYC8C6REMY4E38   
45          3138146  SI7YQSVPFZBSQ878IC17   
50           613400  549300IYKILIU506KA05   
60           987053  549300SCFU7K14E0J331   
65          2787770  549300XV8D5BHDJZY155   
69          1001648  549300CP7747DCRW6U68   
78          1407932  8VPESZVIXN83ENVWIB56   
80          3101065  549300WJMSK78N2L9U23   
85          3384318  549300LS4IRCYZSRMH20   
89           121642  549300SFG15JDKI5MD22   
98           633378  549300N6U5XCH70TOK35   
111          352772  WE0I402RW25AU38DTI13   
119          428547  549300UDBUNBNEKR8J69   
157         3938186  BFLFJ4PXRGDML87ZYT33   
179          355858  254900OD9TDRYGWJ0N48   
194         3706013  549300UZLRT6BCR3ZQ32   
199          693224  549300ZTT08EKQRVTR15   
200         1011526  549300KJZ82173UB3I21   
229         3378018  KWYT8OG5TS2HT583WG93   
232          618807  5493006NTCY0P06JR884   
238          924405  549300RWP6SKF6EZZP82   
247          290052  549300CFJHGA40RI7O81   
281         2652092  WVM1F03F86RQLLTEVE84   
312         2391588  549300Y6FW0UWRZJW587   
361         3376733  549300QLL0WGOPA6R131   
362         3696936  54930041WT62XX21KC11   
368          342634  01J4SO3XTWZF4PP38209   
384          955753  549300RP0N2VARTRFQ77   
387         1008674  549300BNF48S5Z88UL34   
416          806846  254900DTLB5WWMBJAD86   
420          269058  549300YSKDQJCQKT0775   
425         3612525  549300B3O78O3WRVJJ49   
439          201834  549300DUTN4RUBI81Z18   
466          176642  213800XA5M2HOWATHG59   
512          399517  549300NBFK4GO76FTE84   
531          212465  OX3PU53ZLPQKJ4700D47   
548          837608  54930040WE4NGYGGO143   
552         3599970  549300Q1TKVLSYVS7C09   
558          811046  II61D6IY86YZ37HBBL25   
560          303550  0L0W72STJN2EGP1X2N39   
562          547840  LBIZXW7X2N50PETIH863   
570         2339795  01ERPZV3DOLNXY2MLB90   
575          804338  5493005SBCJ71Z4XVY11   
576         2743244  5493006QG55R8V712J33   
579          814430  GDN5JXQ4P5NZE28ZRC90   
583          595869  FT6J43S06X6CLJ0R0B48   
592         2515320  549300J3KQJDSZQIMM59   
610         1093317  549300L0EV5UM3IRHJ33   
619         1002430  549300ZC90ZINB3GMG04   
646          537449  549300F247N2IU8SC024   
667         2958972  5493008S6MTNE6CY5G37   
677         3187612  549300AF1DMBPMDRP146   
690         3212149  549300GWD9H4FQ2VR805   
692          716833  549300QX0QWWJKEY4R28   
696          416245  549300O7SGM8FH65GQ47   
708          353555  549300ASIS4D2QDWH380   
713          264772  549300DFPDZFD8DWQX71   
721           30502  549300MKT4KNKP08CQ45   
724         3275939  5493000V7431YLIMOX56   
751         1436204  549300EGL1VV7LY0QU69   
770          139740  89Z2WRK82BORVH42CP71   
777          451965  KB1H1DSPRFMYMCUFXT09   
788          132554  549300X3PFQJ32XJSB27   
790         3470985  549300DCFF8W6ZAEKH70   
809          967046  549300ZLAWM1M5QAJH43   
811          808176  H98JYKDFKFZ5ZPCSMT69   
824          121679  549300JZOEFUDT8C2R43   
858          631570  549300VRYDYOPWK5MO08   
885          143662  IFQSIUC9AGQV2NE8CN25   
897          905673  549300QYX5EMLSR68B45   
905          675332  IYDOJBGJWY9T8XKCSX06   
914          687009  549300ZJ3ZL66QGSGO48   
930         2756767  549300TU1SISIUY3SK49   
938         1145476  KMRURHT0VWKYS6Z5KU67   
944          635907  54930061YDWSR567KC82   
947          854052  549300SXFX3WEL5ERY54   
955          968070  549300C61LNGA8J8EF85   
958          299046  549300OUV501REVTQ527   
964          455552  549300NQ6JHMRWQ5IH65   
969          197478  F28JOQ8OBWCFUYM0UX93   
986          865450  5493001RCW6RN8X6X688   
992          825146  549300SNZET0P5BZ3J56   


In [11]:
print(len(check_df[display_cols][(check_df.respondent_city==check_df.legal_city)&(~check_df.legal_city.isin(["nan","-1"]))]), "rows matched on city")
check_df[display_cols][(check_df.respondent_city==check_df.legal_city)&(~check_df.legal_city.isin(["nan","-1"]))]

512 rows matched on city


institution_id                id_lei  \
2           3603765  549300XVXVMZ9CDXV530   
5           2871099  549300LTKCJV903ZQR25   
26           550635  549300NN5CG5Q640OV05   
31           474919  DZC62HF6UIZYJ08V1J90   
32           920854  54930002ZF7XTZGVKY26   
42           302656  549300WYC8C6REMY4E38   
45          3138146  SI7YQSVPFZBSQ878IC17   
50           613400  549300IYKILIU506KA05   
60           987053  549300SCFU7K14E0J331   
65          2787770  549300XV8D5BHDJZY155   
69          1001648  549300CP7747DCRW6U68   
78          1407932  8VPESZVIXN83ENVWIB56   
85          3384318  549300LS4IRCYZSRMH20   
89           121642  549300SFG15JDKI5MD22   
111          352772  WE0I402RW25AU38DTI13   
141          687951  5493005A0757T9GRRI44   
157         3938186  BFLFJ4PXRGDML87ZYT33   
160          722777  TR24TWEY5RVRQV65HD49   
194         3706013  549300UZLRT6BCR3ZQ32   
199          693224  549300ZTT08EKQRVTR15   
200         1011526  549300KJZ82173UB3I21   
232          618807  5493006NTCY0P06JR884   
247          290052  549300CFJHGA40RI7O81   
275          956255  VUAW1MW1BHNL595RH698   
281         2652092  WVM1F03F86RQLLTEVE84   
312         2391588  549300Y6FW0UWRZJW587   
361         3376733  549300QLL0WGOPA6R131   
362         3696936  54930041WT62XX21KC11   
368          342634  01J4SO3XTWZF4PP38209   
384          955753  549300RP0N2VARTRFQ77   
387         1008674  549300BNF48S5Z88UL34   
416          806846  254900DTLB5WWMBJAD86   
420          269058  549300YSKDQJCQKT0775   
425         3612525  549300B3O78O3WRVJJ49   
439          201834  549300DUTN4RUBI81Z18   
463          928056  549300QUH5S3VFIWMU57   
466          176642  213800XA5M2HOWATHG59   
512          399517  549300NBFK4GO76FTE84   
531          212465  OX3PU53ZLPQKJ4700D47   
548          837608  54930040WE4NGYGGO143   
552         3599970  549300Q1TKVLSYVS7C09   
558          811046  II61D6IY86YZ37HBBL25   
560          303550  0L0W72STJN2EGP1X2N39   
562          547840  LBIZXW7X2N50PETIH863   
570         2339795  01ERPZV3DOLNXY2MLB90   
575          804338  5493005SBCJ71Z4XVY11   
576         2743244  5493006QG55R8V712J33   
579          814430  GDN5JXQ4P5NZE28ZRC90   
583          595869  FT6J43S06X6CLJ0R0B48   
592         2515320  549300J3KQJDSZQIMM59   
619         1002430  549300ZC90ZINB3GMG04   
646          537449  549300F247N2IU8SC024   
667         2958972  5493008S6MTNE6CY5G37   
677         3187612  549300AF1DMBPMDRP146   
690         3212149  549300GWD9H4FQ2VR805   
692          716833  549300QX0QWWJKEY4R28   
696          416245  549300O7SGM8FH65GQ47   
708          353555  549300ASIS4D2QDWH380   
713          264772  549300DFPDZFD8DWQX71   
721           30502  549300MKT4KNKP08CQ45   
724         3275939  5493000V7431YLIMOX56   
740          339072  549300EMNQ2QLOEPQ289   
770          139740  89Z2WRK82BORVH42CP71   
777          451965  KB1H1DSPRFMYMCUFXT09   
784          326858  Q107R4XFOZ6F6K73C488   
788          132554  549300X3PFQJ32XJSB27   
790         3470985  549300DCFF8W6ZAEKH70   
809          967046  549300ZLAWM1M5QAJH43   
811          808176  H98JYKDFKFZ5ZPCSMT69   
824          121679  549300JZOEFUDT8C2R43   
858          631570  549300VRYDYOPWK5MO08   
885          143662  IFQSIUC9AGQV2NE8CN25   
892         1000100  549300COSKD1GGV2KI91   
897          905673  549300QYX5EMLSR68B45   
905          675332  IYDOJBGJWY9T8XKCSX06   
914          687009  549300ZJ3ZL66QGSGO48   
930         2756767  549300TU1SISIUY3SK49   
944          635907  54930061YDWSR567KC82   
947          854052  549300SXFX3WEL5ERY54   
955          968070  549300C61LNGA8J8EF85   
958          299046  549300OUV501REVTQ527   
964          455552  549300NQ6JHMRWQ5IH65   
969          197478  F28JOQ8OBWCFUYM0UX93   
986          865450  5493001RCW6RN8X6X688   
992          825146  549300SNZET0P5BZ3J56   
995          606046  Q7C315HKI8VX0SSKBS64   
1005         627425  549300WI0D85GPCMEM61   
1024        2119773  9LIMABRJ9VPV74PBJB17   


In [12]:
#simple fuzz metrics
check_df['name_simple_fuzz'] = check_df.apply(lambda x: fuzz.ratio(x.nm_lgl, x.legal_name), axis=1)
check_df['city_simple_fuzz'] = check_df.apply(lambda x: fuzz.ratio(x.city, x.legal_city), axis=1)
check_df['street_simple_fuzz'] = check_df.apply(lambda x: fuzz.ratio(x.street_line1, x.legal_street1), axis=1)
#legal_name vs nm_lgl
#city and legal city
#street_line1 vs legal_street1
display_cols.append('name_simple_fuzz')
display_cols.append('city_simple_fuzz')
display_cols.append('street_simple_fuzz')
check_df[display_cols].sort_values(['name_simple_fuzz', 'city_simple_fuzz', 'street_simple_fuzz'], ascending=False)

institution_id                id_lei  \
5           2871099  549300LTKCJV903ZQR25   
26           550635  549300NN5CG5Q640OV05   
78          1407932  8VPESZVIXN83ENVWIB56   
85          3384318  549300LS4IRCYZSRMH20   
157         3938186  BFLFJ4PXRGDML87ZYT33   
194         3706013  549300UZLRT6BCR3ZQ32   
247          290052  549300CFJHGA40RI7O81   
281         2652092  WVM1F03F86RQLLTEVE84   
361         3376733  549300QLL0WGOPA6R131   
362         3696936  54930041WT62XX21KC11   
387         1008674  549300BNF48S5Z88UL34   
420          269058  549300YSKDQJCQKT0775   
425         3612525  549300B3O78O3WRVJJ49   
439          201834  549300DUTN4RUBI81Z18   
466          176642  213800XA5M2HOWATHG59   
531          212465  OX3PU53ZLPQKJ4700D47   
548          837608  54930040WE4NGYGGO143   
558          811046  II61D6IY86YZ37HBBL25   
562          547840  LBIZXW7X2N50PETIH863   
570         2339795  01ERPZV3DOLNXY2MLB90   
575          804338  5493005SBCJ71Z4XVY11   
576         2743244  5493006QG55R8V712J33   
579          814430  GDN5JXQ4P5NZE28ZRC90   
583          595869  FT6J43S06X6CLJ0R0B48   
619         1002430  549300ZC90ZINB3GMG04   
646          537449  549300F247N2IU8SC024   
677         3187612  549300AF1DMBPMDRP146   
692          716833  549300QX0QWWJKEY4R28   
696          416245  549300O7SGM8FH65GQ47   
708          353555  549300ASIS4D2QDWH380   
721           30502  549300MKT4KNKP08CQ45   
724         3275939  5493000V7431YLIMOX56   
770          139740  89Z2WRK82BORVH42CP71   
777          451965  KB1H1DSPRFMYMCUFXT09   
788          132554  549300X3PFQJ32XJSB27   
790         3470985  549300DCFF8W6ZAEKH70   
809          967046  549300ZLAWM1M5QAJH43   
811          808176  H98JYKDFKFZ5ZPCSMT69   
824          121679  549300JZOEFUDT8C2R43   
858          631570  549300VRYDYOPWK5MO08   
930         2756767  549300TU1SISIUY3SK49   
947          854052  549300SXFX3WEL5ERY54   
955          968070  549300C61LNGA8J8EF85   
1024        2119773  9LIMABRJ9VPV74PBJB17   
1045        3262788  5493004IEEY3EWUVQH38   
1092         366078  5493001ZYMBN3CK8LJ82   
1198         819855  549300X7PN8KSYQHY415   
1208        3013823  549300PZXSGE8V4F6I85   
1212         376442  549300CWJ74FF73VDL12   
1216         499453  549300F5TN705NCHGW39   
1241         217059  549300TIX8J3RRFKXZ81   
1249        3165357  549300Z6RK4QCIMZJD44   
1253        3487518  D8SFNSSIDZMKUS9I1S65   
1269         507509  549300YFPHIE78XPP635   
1275         722544  5493006P0JVBBAHVXV08   
1326         601050  7DMUJTL9FFTVIAG9H788   
1328         520003  549300D7AV8NGI6N3S98   
1354         340256  549300M3TJGNW53OWQ30   
1370          37640  5493002JDOI3GTNVUD76   
1380         633677  549300KM534EBXZB8F72   
1382         812557  549300J9E3YDKIBPUY45   
1430         985479  549300WLYZ63QPFTDP84   
1471         656733  YJMYTIGWK1HM7EQ06C15   
1504        2358769  549300LH06ZZHKPX5U83   
1532         269049  254900040LMONERSH242   
1575        2445052  54930072FD7HWWJL4E65   
1577         613008  TKT6FH38184ZYBTPKS77   
1618         128904  X8V2II80XTQHRH7NCB19   
1652         642549  O4XVIZ10YPQYFKUKCF76   
1657        4165907  549300B95782G2DYRD47   
1683         479839  549300EEYVCFG0V6Z057   
1717        2634191  549300ESRQ6OLBB56N04   
1740         274829  549300TELLWSMYL9RE90   
1821        3207921  549300925HE78SR7H984   
1826         371223  549300QHPJ9CLOLCVE82   
1846         200640  549300PCCKR7GKQPTC92   
1858         506249  549300ZQKLX5VHD8E865   
1859         453147  549300G0J6GTFXLL2C41   
1863         540926  549300K7EA6G6K9GYL80   
1866         875655  549300Z1WVL6I1S59C42   
1911         957757  549300COZ9YQTC4J1378   
1929         901134  549300RMW817W08PUN16   
1979        3717167  549300M0PD2X63HUPF20   
1989         524971  5493002XHCZ94X8YST31   
1997         956956  549300575R17XN3DXK30   
2020         703552  549300I23OUVH341T124   
2092        3294583  549300BKE6IT7LYIF705   
2202         396057  549300OBOL474MATJ593   


In [13]:
#fuzz.partial_ratio("this is a test", "this is a test!")
#fuzz.ratio("fuzzy wuzzy was a bear", "wuzzy fuzzy was a bear")
#fuzz.token_sort_ratio("fuzzy was a bear", "fuzzy fuzzy was a bear")
check_df[display_cols].sort_values(['name_simple_fuzz', 'city_simple_fuzz', 'street_simple_fuzz'], ascending=False)


institution_id                id_lei  \
5           2871099  549300LTKCJV903ZQR25   
26           550635  549300NN5CG5Q640OV05   
78          1407932  8VPESZVIXN83ENVWIB56   
85          3384318  549300LS4IRCYZSRMH20   
157         3938186  BFLFJ4PXRGDML87ZYT33   
194         3706013  549300UZLRT6BCR3ZQ32   
247          290052  549300CFJHGA40RI7O81   
281         2652092  WVM1F03F86RQLLTEVE84   
361         3376733  549300QLL0WGOPA6R131   
362         3696936  54930041WT62XX21KC11   
387         1008674  549300BNF48S5Z88UL34   
420          269058  549300YSKDQJCQKT0775   
425         3612525  549300B3O78O3WRVJJ49   
439          201834  549300DUTN4RUBI81Z18   
466          176642  213800XA5M2HOWATHG59   
531          212465  OX3PU53ZLPQKJ4700D47   
548          837608  54930040WE4NGYGGO143   
558          811046  II61D6IY86YZ37HBBL25   
562          547840  LBIZXW7X2N50PETIH863   
570         2339795  01ERPZV3DOLNXY2MLB90   
575          804338  5493005SBCJ71Z4XVY11   
576         2743244  5493006QG55R8V712J33   
579          814430  GDN5JXQ4P5NZE28ZRC90   
583          595869  FT6J43S06X6CLJ0R0B48   
619         1002430  549300ZC90ZINB3GMG04   
646          537449  549300F247N2IU8SC024   
677         3187612  549300AF1DMBPMDRP146   
692          716833  549300QX0QWWJKEY4R28   
696          416245  549300O7SGM8FH65GQ47   
708          353555  549300ASIS4D2QDWH380   
721           30502  549300MKT4KNKP08CQ45   
724         3275939  5493000V7431YLIMOX56   
770          139740  89Z2WRK82BORVH42CP71   
777          451965  KB1H1DSPRFMYMCUFXT09   
788          132554  549300X3PFQJ32XJSB27   
790         3470985  549300DCFF8W6ZAEKH70   
809          967046  549300ZLAWM1M5QAJH43   
811          808176  H98JYKDFKFZ5ZPCSMT69   
824          121679  549300JZOEFUDT8C2R43   
858          631570  549300VRYDYOPWK5MO08   
930         2756767  549300TU1SISIUY3SK49   
947          854052  549300SXFX3WEL5ERY54   
955          968070  549300C61LNGA8J8EF85   
1024        2119773  9LIMABRJ9VPV74PBJB17   
1045        3262788  5493004IEEY3EWUVQH38   
1092         366078  5493001ZYMBN3CK8LJ82   
1198         819855  549300X7PN8KSYQHY415   
1208        3013823  549300PZXSGE8V4F6I85   
1212         376442  549300CWJ74FF73VDL12   
1216         499453  549300F5TN705NCHGW39   
1241         217059  549300TIX8J3RRFKXZ81   
1249        3165357  549300Z6RK4QCIMZJD44   
1253        3487518  D8SFNSSIDZMKUS9I1S65   
1269         507509  549300YFPHIE78XPP635   
1275         722544  5493006P0JVBBAHVXV08   
1326         601050  7DMUJTL9FFTVIAG9H788   
1328         520003  549300D7AV8NGI6N3S98   
1354         340256  549300M3TJGNW53OWQ30   
1370          37640  5493002JDOI3GTNVUD76   
1380         633677  549300KM534EBXZB8F72   
1382         812557  549300J9E3YDKIBPUY45   
1430         985479  549300WLYZ63QPFTDP84   
1471         656733  YJMYTIGWK1HM7EQ06C15   
1504        2358769  549300LH06ZZHKPX5U83   
1532         269049  254900040LMONERSH242   
1575        2445052  54930072FD7HWWJL4E65   
1577         613008  TKT6FH38184ZYBTPKS77   
1618         128904  X8V2II80XTQHRH7NCB19   
1652         642549  O4XVIZ10YPQYFKUKCF76   
1657        4165907  549300B95782G2DYRD47   
1683         479839  549300EEYVCFG0V6Z057   
1717        2634191  549300ESRQ6OLBB56N04   
1740         274829  549300TELLWSMYL9RE90   
1821        3207921  549300925HE78SR7H984   
1826         371223  549300QHPJ9CLOLCVE82   
1846         200640  549300PCCKR7GKQPTC92   
1858         506249  549300ZQKLX5VHD8E865   
1859         453147  549300G0J6GTFXLL2C41   
1863         540926  549300K7EA6G6K9GYL80   
1866         875655  549300Z1WVL6I1S59C42   
1911         957757  549300COZ9YQTC4J1378   
1929         901134  549300RMW817W08PUN16   
1979        3717167  549300M0PD2X63HUPF20   
1989         524971  5493002XHCZ94X8YST31   
1997         956956  549300575R17XN3DXK30   
2020         703552  549300I23OUVH341T124   
2092        3294583  549300BKE6IT7LYIF705   
2202         396057  549300OBOL474MATJ593   


In [14]:
print(len(check_df[check_df.name_simple_fuzz>90]), "simple name match")
print(len(check_df[check_df.city_simple_fuzz>90]), "simple city match")
print(len(check_df[check_df.street_simple_fuzz>90]), "simple street match")

488 simple name match
515 simple city match
361 simple street match


In [15]:
print(len(check_df[(check_df.city_simple_fuzz>90)&(check_df.street_simple_fuzz>90)]), "city and street")

349 city and street


In [19]:
#pull LEI based on match criteria over 90
    #legal_name vs nm_lgl
    #city and legal city
    #street_line1 vs legal_street1
#put fuzz stuffs
#for row in panel
    #create fuzzy metrics
        #loop over gleif relevant column
        #choose with highest match
    #if fuzzy metrics >= 90
        #copy LEI in from GLEIF
fuzzy_list = []
high_score = 0
for index, row in nic_ids.iterrows():
    print(index)
    for g_index, g_row in gleif_df.iterrows():
        
        city_match_score = fuzz.ratio(row.nm_lgl, g_row.legal_name)
        street_match_score = fuzz.ratio(row.street_line1, g_row.legal_street1)
        name_match_score = fuzz.ratio(row.nm_lgl, g_row.legal_name)
        total_score = city_match_score + street_match_score + name_match_score
        if total_score > high_score:
            high_score = total_score
        #if city_match_score >=85 and street_match_score>=85 and name_match_score>=85:
            #print(city_match_score, "city")
            fuzzy_list.append({
                "inst_id":row.institution_id,
                "nic_name":row.nm_lgl,
                "gleif_name":g_row.legal_name,
                "nic_lei":row.id_lei,
                "gleif_lei":g_row.id_lei,
                "panel_city":row.respondent_city,
                "gleif_city":g_row.legal_city,
                "panel_street":row.street_line1,
                "gleif_street":g_row.legal_street1,
                "city_score":city_match_score,
                "street_score":street_match_score,
                "name_score":name_match_score
            })


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1861
1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060


3500
3501
3502
3503
3504
3505
3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699


5139
5140
5141
5142
5143
5144
5145
5146
5147
5148
5149
5150
5151
5152
5153
5154
5155
5156
5157
5158
5159
5160
5161
5162
5163
5164
5165
5166
5167
5168
5169
5170
5171
5172
5173
5174
5175
5176
5177
5178
5179
5180
5181
5182
5183
5184
5185
5186
5187
5188
5189
5190
5191
5192
5193
5194
5195
5196
5197
5198
5199
5200
5201
5202
5203
5204
5205
5206
5207
5208
5209
5210
5211
5212
5213
5214
5215
5216
5217
5218
5219
5220
5221
5222
5223
5224
5225
5226
5227
5228
5229
5230
5231
5232
5233
5234
5235
5236
5237
5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338


In [ ]:
gleif_df.columns

In [ ]:
nic_ids.columns

In [20]:
fuzzy_df = pd.DataFrame(fuzzy_list)
fuzzy_df.to_csv("../output/fuzzy_first_run.txt", index=False, sep="|")

In [21]:
fuzzy_df.head()

city_score    gleif_city             gleif_lei  \
0           0    WILMINGTON  21380087BAB79DFYRR32   
1           0  PHILADELPHIA  213800XHK9QDTG1R6S96   
2           7    WILMINGTON  21380048FCCD1JYL8J91   
3          15    WILMINGTON  213800YAB57IJOMFLZ57   
4          17  SANTA MONICA  213800S66WA6ACL6L143   

                              gleif_name                  gleif_street  \
0                    LION COMMERCIAL LLC         108, WEST 13TH STREET   
1  WISSAHICKON REAL ESTATE ALLIANCE, LLC            1500 WALNUT STREET   
2             SFR 2010-3 ACQUISITION LLC         2711 CENTREVILLE ROAD   
3                            SLRB-I, LLC   CORPORATION SERVICE COMPANY   
4                             180LA, LLC  1733 OCEAN AVENUE, 4TH FLOOR   

  inst_id  name_score nic_lei nic_name   panel_city panel_street  street_score  
0  546991           0      -1       -1  LEAVENWORTH           -1             9  
1  546991           0      -1       -1  LEAVENWORTH           -1            10  
2  546991           7      -1       -1  LEAVENWORTH           -1             9  
3  546991          15      -1       -1  LEAVENWORTH           -1             0  
4  546991          17      -1       -1  LEAVENWORTH           -1             7

In [24]:
fuzzy_df = fuzzy_df[['inst_id','nic_lei', 'gleif_lei',
                    'nic_name','gleif_name', 'name_score',
                      'panel_city', 'gleif_city', 'city_score',
                      'panel_street', 'gleif_street','street_score']]

In [26]:
fuzzy_df.head(40)

inst_id               nic_lei             gleif_lei  \
0    546991                    -1  21380087BAB79DFYRR32   
1    546991                    -1  213800XHK9QDTG1R6S96   
2    546991                    -1  21380048FCCD1JYL8J91   
3    546991                    -1  213800YAB57IJOMFLZ57   
4    546991                    -1  213800S66WA6ACL6L143   
5    546991                    -1  213800OG4MHQSSFI8Y75   
6    546991                    -1  529900WFHX6GRPXLBU31   
7    546991                    -1  2549003OZMJYWXFF9S60   
8    546991                    -1  254900N96TMY2BDW4S57   
9    546991                    -1  254900RC7KXX8I79YV78   
10   546991                    -1  549300GYWE9LWAHBN706   
11  3603765  549300XVXVMZ9CDXV530  2138008LTICA91ZQKQ29   
12  3603765  549300XVXVMZ9CDXV530  213800NAN42LNYBD1Z52   
13  3603765  549300XVXVMZ9CDXV530  213800HKAADHE5IWM916   
14  3603765  549300XVXVMZ9CDXV530  2138002Z7YAJAKZFUK85   
15  3603765  549300XVXVMZ9CDXV530  213800IMDG729RLSUM04   
16  3603765  549300XVXVMZ9CDXV530  213800P7IFUPXLSI3O07   
17  3603765  549300XVXVMZ9CDXV530  213800KOH9RK6QT97D37   
18  3603765  549300XVXVMZ9CDXV530  213800QC7QOOVXBCE436   
19  3603765  549300XVXVMZ9CDXV530  2138003T2AVNIFKAIA36   
20  3603765  549300XVXVMZ9CDXV530  213800MWCCDADP38AW10   
21  3603765  549300XVXVMZ9CDXV530  21380055IMHX3N5UL146   
22  3603765  549300XVXVMZ9CDXV530  529900O8P8I2P84ZTJ92   
23  3603765  549300XVXVMZ9CDXV530  25490052T4M68YYACN14   
24  3603765  549300XVXVMZ9CDXV530  254900NLUIQMYI2MW872   
25  3603765  549300XVXVMZ9CDXV530  254900UKANDAKWQ7CR03   
26  2871099  549300LTKCJV903ZQR25  254900ARLAZ571P0Z136   
27  2871099  549300LTKCJV903ZQR25  254900KN1X8B3CQDSO97   
28  2871099  549300LTKCJV903ZQR25  254900MDBTY5G03LIX66   
29   474919  DZC62HF6UIZYJ08V1J90  1IE8VN30JCEQV1H4R804   
30   428547  549300UDBUNBNEKR8J69  213800GF3VF8WSF5Q651   
31  3938186  BFLFJ4PXRGDML87ZYT33  549300APS6VPRJNHGH77   
32  3938186  BFLFJ4PXRGDML87ZYT33  1IE8VN30JCEQV1H4R804   
33   924405  549300RWP6SKF6EZZP82  213800XA5M2HOWATHG59   
34   176642  213800XA5M2HOWATHG59  213800XA5M2HOWATHG59   

                             nic_name  \
0                                  -1   
1                                  -1   
2                                  -1   
3                                  -1   
4                                  -1   
5                                  -1   
6                                  -1   
7                                  -1   
8                                  -1   
9                                  -1   
10                                 -1   
11                   ADAMS DAIRY BANK   
12                   ADAMS DAIRY BANK   
13                   ADAMS DAIRY BANK   
14                   ADAMS DAIRY BANK   
15                   ADAMS DAIRY BANK   
16                   ADAMS DAIRY BANK   
17                   ADAMS DAIRY BANK   
18                   ADAMS DAIRY BANK   
19                   ADAMS DAIRY BANK   
20                   ADAMS DAIRY BANK   
21                   ADAMS DAIRY BANK   
22                   ADAMS DAIRY BANK   
23                   ADAMS DAIRY BANK   
24                   ADAMS DAIRY BANK   
25                   ADAMS DAIRY BANK   
26                       TRISTAR BANK   
27                       TRISTAR BANK   
28                       TRISTAR BANK   
29  FULTON BANK, NATIONAL ASSOCIATION   
30   ST. CHARLES BANK & TRUST COMPANY   
31   BANKUNITED, NATIONAL ASSOCIATION   
32   BANKUNITED, NATIONAL ASSOCIATION   
33                DIME COMMUNITY BANK   
34                 LNB COMMUNITY BANK   

                                     gleif_name  name_score     panel_city  \
0                           LION COMMERCIAL LLC           0    LEAVENWORTH   
1         WISSAHICKON REAL ESTATE ALLIANCE, LLC           0    LEAVENWORTH   
2                    SFR 2010-3 ACQUISITION LLC           7    LEAVENWORTH   
3                                   SLRB-I, LLC          15    LEAVENWORTH   
4           